## Linking a dataset of real historical persons

In this example, we deduplicate a more realistic dataset. The data is based on historical persons scraped from wikidata. Duplicate records are introduced with a variety of errors introduced.


<a target="_blank" href="https://colab.research.google.com/github/moj-analytical-services/splink/blob/splink4_dev/docs/demos/examples/duckdb/deduplicate_50k_synthetic.ipynb">
  <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/>
</a>


In [100]:
# Uncomment and run this cell if you're running in Google Colab.
# !pip install git+https://github.com/moj-analytical-services/splink.git@splink4_dev

In [101]:
from splink import splink_datasets

df = splink_datasets.historical_50k

In [102]:
df.head()

unique_id   cluster                                         full_name  \
0  Q2296770-1  Q2296770  thomas clifford, 1st baron clifford of chudleigh   
1  Q2296770-2  Q2296770                               thomas of chudleigh   
2  Q2296770-3  Q2296770               tom 1st baron clifford of chudleigh   
3  Q2296770-4  Q2296770                              thomas 1st chudleigh   
4  Q2296770-5  Q2296770              thomas clifford, 1st baron chudleigh   

  first_and_surname first_name    surname         dob birth_place  \
0  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
1  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
2     tom chudleigh        tom  chudleigh  1630-08-01       devon   
3  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
4  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   

  postcode_fake gender  occupation  
0      tq13 8df   male  politician  
1      tq13 8df   male  politician  
2      tq13 8df   male  politician  
3      tq13 8hu   None  politician  
4      tq13 8df   None  politician

In [103]:
from splink import DuckDBAPI
from splink.exploratory import profile_columns

db_api = DuckDBAPI()
profile_columns(df, db_api, column_expressions=["first_name", "substr(surname,1,2)"])

alt.VConcatChart(...)

In [104]:
from splink import DuckDBAPI, block_on
from splink.blocking_analysis import (
    cumulative_comparisons_to_be_scored_from_blocking_rules_chart,
)

blocking_rules = [
    block_on("substr(first_name,1,3)", "substr(surname,1,4)"),
    block_on("surname", "dob"),
    block_on("first_name", "dob"),
    block_on("postcode_fake", "first_name"),
    block_on("postcode_fake", "surname"),
    block_on("dob", "birth_place"),
    block_on("substr(postcode_fake,1,3)", "dob"),
    block_on("substr(postcode_fake,1,3)", "first_name"),
    block_on("substr(postcode_fake,1,3)", "surname"),
    block_on("substr(first_name,1,2)", "substr(surname,1,2)", "substr(dob,1,4)"),
]

db_api = DuckDBAPI()

cumulative_comparisons_to_be_scored_from_blocking_rules_chart(
    table_or_tables=df,
    blocking_rules=blocking_rules,
    db_api=db_api,
    link_type="dedupe_only",
)

alt.Chart(...)

In [105]:
import splink.comparison_library as cl

from splink import Linker, SettingsCreator

settings = SettingsCreator(
    link_type="dedupe_only",
    blocking_rules_to_generate_predictions=blocking_rules,
    comparisons=[
        cl.ForenameSurnameComparison(
            "first_name",
            "surname",
            forename_surname_concat_col_name="first_name_surname_concat",
        ),
        cl.DateOfBirthComparison(
            "dob", input_is_string=True, separate_1st_january=True
        ),
        cl.PostcodeComparison("postcode_fake"),
        cl.ExactMatch("birth_place").configure(term_frequency_adjustments=True),
        cl.ExactMatch("occupation").configure(term_frequency_adjustments=True),
    ],
    retain_intermediate_calculation_columns=True,
)
# Needed to apply term frequencies to first+surname comparison
df["first_name_surname_concat"] = df["first_name"] + " " + df["surname"]
linker = Linker(df, settings, database_api=db_api)

In [106]:
linker.training.estimate_probability_two_random_records_match(
    [
        "l.first_name = r.first_name and l.surname = r.surname and l.dob = r.dob",
        "substr(l.first_name,1,2) = substr(r.first_name,1,2) and l.surname = r.surname and substr(l.postcode_fake,1,2) = substr(r.postcode_fake,1,2)",
        "l.dob = r.dob and l.postcode_fake = r.postcode_fake",
    ],
    recall=0.6,
)

Probability two random records match is estimated to be  0.000136.
This means that amongst all possible pairwise record comparisons, one in 7,362.31 are expected to match.  With 1,279,041,753 total possible comparisons, we expect a total of around 173,728.33 matching pairs


In [107]:
linker.training.estimate_u_using_random_sampling(max_pairs=5e6)

----- Estimating u probabilities using random sampling -----


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

u probability not trained for first_name_surname - Match on reversed cols: first_name and surname (comparison vector value: 5). This usually means the comparison level was never observed in the training data.

Estimated u probabilities using random sampling

Your model is not yet fully trained. Missing estimates for:
    - first_name_surname (some u values are not trained, no m values are trained).
    - dob (no m values are trained).
    - postcode_fake (no m values are trained).
    - birth_place (no m values are trained).
    - occupation (no m values are trained).


In [108]:
training_blocking_rule = block_on("first_name", "surname")
training_session_names = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
(l."first_name" = r."first_name") AND (l."surname" = r."surname")

Parameter estimates will be made for the following comparison(s):
    - dob
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - first_name_surname

Iteration 1: Largest change in params was -0.543 in the m_probability of dob, level `Exact match on year (1st of January only)`
Iteration 2: Largest change in params was -0.0967 in the m_probability of postcode_fake, level `Exact match on postcode_fake`
Iteration 3: Largest change in params was 0.0244 in the m_probability of birth_place, level `All other comparisons`
Iteration 4: Largest change in params was -0.0107 in the m_probability of birth_place, level `Exact match on birth_place`
Iteration 5: Largest change in params was 0.0055 in the m_probability

In [109]:
training_blocking_rule = block_on("dob")
training_session_dob = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
l."dob" = r."dob"

Parameter estimates will be made for the following comparison(s):
    - first_name_surname
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - dob


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))


Iteration 1: Largest change in params was -0.516 in the m_probability of first_name_surname, level `Exact match on first_name_surname_concat`
Iteration 2: Largest change in params was 0.0224 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 3: Largest change in params was 0.00609 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 4: Largest change in params was 0.00174 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 5: Largest change in params was 0.00052 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 6: Largest change in params was 0.00016 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 7: Largest change in params was 5.01e-05 in the m_probability of first_name_surname, level `All other comparisons`

EM converged after 7 iterations

Your model is not yet fully trained. Missing estimates for:
    - first_name_su

The final match weights can be viewed in the match weights chart:


In [110]:
linker.visualisations.match_weights_chart()

alt.VConcatChart(...)

In [111]:
linker.evaluation.unlinkables_chart()

alt.LayerChart(...)

In [112]:
df_predict = linker.inference.predict()
df_e = df_predict.as_pandas_dataframe(limit=5)
df_e

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))


 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


match_weight  match_probability   unique_id_l  unique_id_r   surname_l  \
0    -30.695245       5.751889e-10   Q16198745-7  Q57312657-7       kerry   
1    -30.695245       5.751889e-10    Q2739999-3  Q27917038-7  lillywhite   
2    -30.695245       5.751889e-10  Q15497183-11  Q28935241-6     collins   
3    -30.695245       5.751889e-10    Q2739999-2  Q27917038-7  lillywhite   
4    -30.695245       5.751889e-10   Q16198745-4  Q57312657-7       kerry   

   surname_r first_name_l first_name_r first_name_surname_concat_l  \
0       kerr      francis        frank               francis kerry   
1  lillicrap        james        jamew            james lillywhite   
2    collyer      william       willie             william collins   
3  lillicrap        james        jamew            james lillywhite   
4       kerr      francis        frank               francis kerry   

  first_name_surname_concat_r  ...  bf_birth_place  bf_tf_adj_birth_place  \
0                  frank kerr  ...        0.166927                    1.0   
1             jamew lillicrap  ...        0.166927                    1.0   
2              willie collyer  ...        0.166927                    1.0   
3             jamew lillicrap  ...        0.166927                    1.0   
4                  frank kerr  ...        0.166927                    1.0   

   occupation_l    occupation_r  gamma_occupation  tf_occupation_l  \
0     cricketer  businessperson                 0         0.121001   
1     cricketer   naval officer                 0         0.121001   
2    politician       cricketer                 0         0.088932   
3     cricketer   naval officer                 0         0.121001   
4     cricketer  businessperson                 0         0.121001   

   tf_occupation_r  bf_occupation  bf_tf_adj_occupation match_key  
0         0.015738       0.107584                   1.0         0  
1         0.009451       0.107584                   1.0         0  
2         0.121001       0.107584                   1.0         0  
3         0.009451       0.107584                   1.0         0  
4         0.015738       0.107584                   1.0         0  

[5 rows x 42 columns]

You can also view rows in this dataset as a waterfall chart as follows:


In [113]:
records_to_plot = df_e.to_dict(orient="records")
linker.visualisations.waterfall_chart(records_to_plot, filter_nulls=False)

alt.LayerChart(...)

In [114]:
clusters = linker.clustering.cluster_pairwise_predictions_at_threshold(
    df_predict, threshold_match_probability=0.95
)

Completed iteration 1, root rows count 671
Completed iteration 2, root rows count 126
Completed iteration 3, root rows count 15
Completed iteration 4, root rows count 4
Completed iteration 5, root rows count 0


In [115]:
from IPython.display import IFrame

linker.visualisations.cluster_studio_dashboard(
    df_predict,
    clusters,
    "dashboards/50k_cluster.html",
    sampling_method="by_cluster_size",
    overwrite=True,
)


IFrame(src="./dashboards/50k_cluster.html", width="100%", height=1200)

In [116]:
linker.evaluation.accuracy_analysis_from_labels_column(
    "cluster", output_type="accuracy", match_weight_round_to_nearest=0.02
)

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))


 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)

In [117]:
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.999,
    include_false_negatives=False,
    include_false_positives=True,
).as_record_dict()
linker.visualisations.waterfall_chart(records)


 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)

In [118]:
# Some of the false negatives will be because they weren't detected by the blocking rules
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.5,
    include_false_negatives=True,
    include_false_positives=False,
).as_record_dict(limit=50)

linker.visualisations.waterfall_chart(records)


 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)